In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.metrics import mean_absolute_percentage_error
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Dropout, BatchNormalization
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from sklearn.multioutput import MultiOutputRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import HistGradientBoostingRegressor
from sklearn.decomposition import PCA
import tensorflow as tf
from tensorflow.keras import layers, models

In [2]:
train_data = pd.read_csv('train.csv')
test_data = pd.read_csv('test.csv')
train_data.head()

Component1_fraction  Component2_fraction  Component3_fraction  \
0                 0.21                 0.00                 0.42   
1                 0.02                 0.33                 0.19   
2                 0.08                 0.08                 0.18   
3                 0.25                 0.42                 0.00   
4                 0.26                 0.16                 0.08   

   Component4_fraction  Component5_fraction  Component1_Property1  \
0                 0.25                 0.12             -0.021782   
1                 0.46                 0.00             -0.224339   
2                 0.50                 0.16              0.457763   
3                 0.07                 0.26             -0.577734   
4                 0.50                 0.00              0.120415   

   Component2_Property1  Component3_Property1  Component4_Property1  \
0              1.981251              0.020036              0.140315   
1              1.148036             -1.107840              0.149533   
2              0.242591             -0.922492              0.908213   
3             -0.930826              0.815284              0.447514   
4              0.666268             -0.626934              2.725357   

   Component5_Property1  ...  BlendProperty1  BlendProperty2  BlendProperty3  \
0              1.032029  ...        0.489143        0.607589        0.321670   
1             -0.354000  ...       -1.257481       -1.475283       -0.437385   
2              0.972003  ...        1.784349        0.450467        0.622687   
3              0.455717  ...       -0.066422        0.483730       -1.865442   
4              0.392259  ...       -0.118913       -1.172398        0.301785   

   BlendProperty4  BlendProperty5  BlendProperty6  BlendProperty7  \
0       -1.236055        1.601132        1.384662        0.305850   
1       -1.402911        0.147941       -1.143244       -0.439171   
2        1.375614       -0.428790        1.161616        0.601289   
3       -0.046295       -0.163820       -0.209693       -1.840566   
4       -1.787407       -0.493361       -0.528049        0.286344   

   BlendProperty8  BlendProperty9  BlendProperty10  
0        0.193460        0.580374        -0.762738  
1       -1.379041       -1.280989        -0.503625  
2        0.872950        0.660000         2.024576  
3        0.300293       -0.351336        -1.551914  
4       -0.265192        0.430513         0.735073  

[5 rows x 65 columns]

In [3]:
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2000 entries, 0 to 1999
Data columns (total 65 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Component1_fraction    2000 non-null   float64
 1   Component2_fraction    2000 non-null   float64
 2   Component3_fraction    2000 non-null   float64
 3   Component4_fraction    2000 non-null   float64
 4   Component5_fraction    2000 non-null   float64
 5   Component1_Property1   2000 non-null   float64
 6   Component2_Property1   2000 non-null   float64
 7   Component3_Property1   2000 non-null   float64
 8   Component4_Property1   2000 non-null   float64
 9   Component5_Property1   2000 non-null   float64
 10  Component1_Property2   2000 non-null   float64
 11  Component2_Property2   2000 non-null   float64
 12  Component3_Property2   2000 non-null   float64
 13  Component4_Property2   2000 non-null   float64
 14  Component5_Property2   2000 non-null   float64
 15  Comp

In [4]:
test_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 56 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   ID                     500 non-null    int64  
 1   Component1_fraction    500 non-null    float64
 2   Component2_fraction    500 non-null    float64
 3   Component3_fraction    500 non-null    float64
 4   Component4_fraction    500 non-null    float64
 5   Component5_fraction    500 non-null    float64
 6   Component1_Property1   500 non-null    float64
 7   Component2_Property1   500 non-null    float64
 8   Component3_Property1   500 non-null    float64
 9   Component4_Property1   500 non-null    float64
 10  Component5_Property1   500 non-null    float64
 11  Component1_Property2   500 non-null    float64
 12  Component2_Property2   500 non-null    float64
 13  Component3_Property2   500 non-null    float64
 14  Component4_Property2   500 non-null    float64
 15  Compon

In [5]:
sample = pd.read_csv('sample_solution.csv')
sample.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ID               500 non-null    int64  
 1   BlendProperty1   500 non-null    float64
 2   BlendProperty2   500 non-null    float64
 3   BlendProperty3   500 non-null    float64
 4   BlendProperty4   500 non-null    float64
 5   BlendProperty5   500 non-null    float64
 6   BlendProperty6   500 non-null    float64
 7   BlendProperty7   500 non-null    float64
 8   BlendProperty8   500 non-null    float64
 9   BlendProperty9   500 non-null    float64
 10  BlendProperty10  500 non-null    float64
dtypes: float64(10), int64(1)
memory usage: 43.1 KB


In [6]:
train_data.head()

Component1_fraction  Component2_fraction  Component3_fraction  \
0                 0.21                 0.00                 0.42   
1                 0.02                 0.33                 0.19   
2                 0.08                 0.08                 0.18   
3                 0.25                 0.42                 0.00   
4                 0.26                 0.16                 0.08   

   Component4_fraction  Component5_fraction  Component1_Property1  \
0                 0.25                 0.12             -0.021782   
1                 0.46                 0.00             -0.224339   
2                 0.50                 0.16              0.457763   
3                 0.07                 0.26             -0.577734   
4                 0.50                 0.00              0.120415   

   Component2_Property1  Component3_Property1  Component4_Property1  \
0              1.981251              0.020036              0.140315   
1              1.148036             -1.107840              0.149533   
2              0.242591             -0.922492              0.908213   
3             -0.930826              0.815284              0.447514   
4              0.666268             -0.626934              2.725357   

   Component5_Property1  ...  BlendProperty1  BlendProperty2  BlendProperty3  \
0              1.032029  ...        0.489143        0.607589        0.321670   
1             -0.354000  ...       -1.257481       -1.475283       -0.437385   
2              0.972003  ...        1.784349        0.450467        0.622687   
3              0.455717  ...       -0.066422        0.483730       -1.865442   
4              0.392259  ...       -0.118913       -1.172398        0.301785   

   BlendProperty4  BlendProperty5  BlendProperty6  BlendProperty7  \
0       -1.236055        1.601132        1.384662        0.305850   
1       -1.402911        0.147941       -1.143244       -0.439171   
2        1.375614       -0.428790        1.161616        0.601289   
3       -0.046295       -0.163820       -0.209693       -1.840566   
4       -1.787407       -0.493361       -0.528049        0.286344   

   BlendProperty8  BlendProperty9  BlendProperty10  
0        0.193460        0.580374        -0.762738  
1       -1.379041       -1.280989        -0.503625  
2        0.872950        0.660000         2.024576  
3        0.300293       -0.351336        -1.551914  
4       -0.265192        0.430513         0.735073  

[5 rows x 65 columns]

In [7]:
target_columns = []
for i in range(1,11):
    target_columns.append(f'BlendProperty{i}')
target_columns

['BlendProperty1',
 'BlendProperty2',
 'BlendProperty3',
 'BlendProperty4',
 'BlendProperty5',
 'BlendProperty6',
 'BlendProperty7',
 'BlendProperty8',
 'BlendProperty9',
 'BlendProperty10']

In [8]:
X = train_data.drop(target_columns,axis = 1)
y = train_data[target_columns]

In [9]:
X_train,X_test, y_train , y_test = train_test_split(X,y,test_size=0.2,shuffle=True,random_state=42)

In [29]:
model = MultiOutputRegressor(RandomForestRegressor())
model.fit(X_train, y_train)  # Y_train shape: (n_samples, 10)
preds = model.predict(X_test)  # shape: (n_samples, 10)

In [20]:
X_train.shape[1]


55

In [30]:
import tensorflow as tf
from tensorflow.keras import layers

# Residual block as a Keras Layer
class ResidualBlock(tf.keras.layers.Layer):
    def __init__(self, units):
        super(ResidualBlock, self).__init__()
        self.dense1 = layers.Dense(units)
        self.bn1 = layers.BatchNormalization()
        self.relu1 = layers.ReLU()
        self.dense2 = layers.Dense(units)
        self.bn2 = layers.BatchNormalization()
        self.relu2 = layers.ReLU()

    def call(self, inputs, training=False):
        x = self.dense1(inputs)
        x = self.bn1(x, training=training)
        x = self.relu1(x)
        x = self.dense2(x)
        x = self.bn2(x, training=training)
        x = layers.add([x, inputs])  # Residual connection
        return self.relu2(x)

# ResNet with 10 hidden layers (5 residual blocks)
def build_resnet(input_dim, hidden_units=128, num_classes=10, num_blocks=5):
    inputs = tf.keras.Input(shape=(input_dim,))
    x = layers.Dense(hidden_units)(inputs)
    x = layers.BatchNormalization()(x)
    x = layers.ReLU()(x)

    for _ in range(num_blocks):
        x = ResidualBlock(hidden_units)(x)

    outputs = layers.Dense(num_classes)(x)
    model = tf.keras.Model(inputs=inputs, outputs=outputs)
    return model

# Example usage
input_dim = X_train.shape[1]  # Replace with X_train.shape[1] in real case
nn = build_resnet(input_dim=input_dim)
nn.summary()

# Compile
nn.compile(
    optimizer='adam',
    loss=calculate_mape,  # or 'sparse_categorical_crossentropy' for classification
    metrics=[evaluate_model]
)


Model: "functional_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_5 (InputLayer)      │ (None, 55)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_27 (Dense)                │ (None, 128)            │         7,168 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_25          │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ re_lu_22 (ReLU)                 │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ residual_block_10               │ (None, 128)            │        34,048 │
│ (ResidualBlock)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ residual_block_11               │ (None, 128)            │        34,048 │
│ (ResidualBlock)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ residual_block_12               │ (None, 128)            │        34,048 │
│ (ResidualBlock)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ residual_block_13               │ (None, 128)            │        34,048 │
│ (ResidualBlock)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ residual_block_14               │ (None, 128)            │        34,048 │
│ (ResidualBlock)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_38 (Dense)                │ (None, 10)             │         1,290 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 179,210 (700.04 KB)

 Trainable params: 176,394 (689.04 KB)

 Non-trainable params: 2,816 (11.00 KB)

In [31]:
early_stop = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=5)

nn.fit(X_train, y_train,
          validation_split=0.1,
          epochs=500,
          batch_size=16,
          callbacks=[early_stop, reduce_lr])

Epoch 1/500


NotImplementedError: Cannot convert a symbolic tf.Tensor (data_1:0) to a numpy array. This error may indicate that you're trying to pass a Tensor to a NumPy call, which is not supported.

In [26]:
nn_preds = nn.predict(X_test)
mse = mean_squared_error(y_test, nn_preds)
r2 = r2_score(y_test, nn_preds)
print("mse : ", mse, "r2 : ", r2)

13/13 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step
mse :  0.23663277924060822 r2 :  0.7641607522964478


In [27]:
# Drop ID column and predict
X_new = test_data.drop('ID', axis=1)
predictions = nn.predict(X_new)

# Get ID column
ID = test_data['ID'].values

# Combine into a DataFrame (columns = ['ID', y1, y2, ..., y10])
submission = pd.DataFrame(predictions, columns=target_columns)
submission.insert(0, 'ID', ID)  # Insert ID as the first column
# Save to CSV
submission.to_csv('submission.csv', index=False)

16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 


In [28]:
submission.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ID               500 non-null    int64  
 1   BlendProperty1   500 non-null    float32
 2   BlendProperty2   500 non-null    float32
 3   BlendProperty3   500 non-null    float32
 4   BlendProperty4   500 non-null    float32
 5   BlendProperty5   500 non-null    float32
 6   BlendProperty6   500 non-null    float32
 7   BlendProperty7   500 non-null    float32
 8   BlendProperty8   500 non-null    float32
 9   BlendProperty9   500 non-null    float32
 10  BlendProperty10  500 non-null    float32
dtypes: float32(10), int64(1)
memory usage: 23.6 KB


In [86]:
sample.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ID               500 non-null    int64  
 1   BlendProperty1   500 non-null    float64
 2   BlendProperty2   500 non-null    float64
 3   BlendProperty3   500 non-null    float64
 4   BlendProperty4   500 non-null    float64
 5   BlendProperty5   500 non-null    float64
 6   BlendProperty6   500 non-null    float64
 7   BlendProperty7   500 non-null    float64
 8   BlendProperty8   500 non-null    float64
 9   BlendProperty9   500 non-null    float64
 10  BlendProperty10  500 non-null    float64
dtypes: float64(10), int64(1)
memory usage: 43.1 KB


In [11]:
# === Step 3: Evaluation Functions ===

def calculate_mape(y_true, y_pred):
    """Use sklearn's MAPE implementation."""
    return mean_absolute_percentage_error(y_true, y_pred)

def calculate_mape_manual(y_true, y_pred):
    """Manual MAPE formula with division safety."""
    y_true = np.array(y_true)
    y_pred = np.array(y_pred)
    mask = y_true != 0
    if not np.any(mask):
        raise ValueError("All true values are zero. MAPE is undefined.")
    return np.mean(np.abs((y_true[mask] - y_pred[mask]) / y_true[mask]))

def calculate_leaderboard_score(mape_cost, leaderboard_type='public'):
    """Leaderboard score: max[10, 100 - (90 × MAPE / Ref Cost)]"""
    reference_costs = {
        'public': 2.72,
        'private': 2.58
    }
    if leaderboard_type not in reference_costs:
        raise ValueError("leaderboard_type must be 'public' or 'private'")
    ref_cost = reference_costs[leaderboard_type]
    score = max(10, 100 - (90 * mape_cost) / ref_cost)
    return score

def evaluate_model(y_true, y_pred, leaderboard_type='public', return_details=False):
    """Evaluate model using MAPE and leaderboard score."""
    mape = calculate_mape(y_true, y_pred)
    score = calculate_leaderboard_score(mape, leaderboard_type)
    if return_details:
        return {
            'mape': mape,
            'leaderboard_score': score,
            'leaderboard_type': leaderboard_type,
            'reference_cost': 2.72 if leaderboard_type == 'public' else 2.58
        }
    return score

# === Step 4: Run Evaluation ===

# Example: Evaluate on full test set
y_true = y_test  # shape: (500, 10)
y_pred = eval_preds  # shape: (500, 10)

# Split for public/private leaderboard
y_true_public = y_true[:250]
y_pred_public = y_pred[:250]

y_true_private = y_true[250:]
y_pred_private = y_pred[250:]

# Compute MAPEs
mape_public = calculate_mape(y_true_public, y_pred_public)
mape_private = calculate_mape(y_true_private, y_pred_private)

# Compute leaderboard scores
public_score = calculate_leaderboard_score(mape_public, leaderboard_type='public')
private_score = calculate_leaderboard_score(mape_private, leaderboard_type='private')

print(f"✅ Public MAPE: {mape_public:.6f}, Score: {public_score:.2f}")
print(f"✅ Private MAPE: {mape_private:.6f}, Score: {private_score:.2f}")

# Optional: Detailed breakdown
detailed_results = evaluate_model(y_true, y_pred, 'public', return_details=True)
print("\n📊 Detailed Evaluation:")
for k, v in detailed_results.items():
    print(f"{k}: {v}")

# === Step 5: Score Curve Example ===

print("\n📈 Score examples for different MAPE values:")
for mape_val in [0.01, 0.05, 0.1, 0.2, 0.5, 1.0, 2.0, 2.5, 3.0]:
    pub = calculate_leaderboard_score(mape_val, 'public')
    priv = calculate_leaderboard_score(mape_val, 'private')
    print(f"MAPE: {mape_val:.2f} → Public: {pub:.2f}, Private: {priv:.2f}")

✅ Public MAPE: 2.981505, Score: 10.00
✅ Private MAPE: 0.824362, Score: 71.24

📊 Detailed Evaluation:
mape: 2.1725764832165417
leaderboard_score: 28.113278128864437
leaderboard_type: public
reference_cost: 2.72

📈 Score examples for different MAPE values:
MAPE: 0.01 → Public: 99.67, Private: 99.65
MAPE: 0.05 → Public: 98.35, Private: 98.26
MAPE: 0.10 → Public: 96.69, Private: 96.51
MAPE: 0.20 → Public: 93.38, Private: 93.02
MAPE: 0.50 → Public: 83.46, Private: 82.56
MAPE: 1.00 → Public: 66.91, Private: 65.12
MAPE: 2.00 → Public: 33.82, Private: 30.23
MAPE: 2.50 → Public: 17.28, Private: 12.79
MAPE: 3.00 → Public: 10.00, Private: 10.00


In [94]:
xgb_model = MultiOutputRegressor(XGBRegressor(n_estimators=500, learning_rate=0.05))
xgb_model.fit(X_train, y_train)

MultiOutputRegressor(estimator=XGBRegressor(base_score=None, booster=None,
                                            callbacks=None,
                                            colsample_bylevel=None,
                                            colsample_bynode=None,
                                            colsample_bytree=None, device=None,
                                            early_stopping_rounds=None,
                                            enable_categorical=False,
                                            eval_metric=None,
                                            feature_types=None,
                                            feature_weights=None, gamma=None,
                                            grow_policy=None,
                                            importance_type=None,
                                            interaction_constraints=None,
                                            learning_rate=0.05, max_bin=None,
                                            max_cat_threshold=None,
                                            max_cat_to_onehot=None,
                                            max_delta_step=None, max_depth=None,
                                            max_leaves=None,
                                            min_child_weight=None, missing=nan,
                                            monotone_constraints=None,
                                            multi_strategy=None,
                                            n_estimators=500, n_jobs=None,
                                            num_parallel_tree=None, ...))

In [95]:
preds_xgb = xgb_model.predict(X_test)

In [ ]:
# Define base regressor
base_lgbm = LGBMRegressor(
    n_estimators=1000,
    learning_rate=0.05,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42,
    n_jobs=-1
)

# Wrap in MultiOutputRegressor for multi-target regression
model = MultiOutputRegressor(base_lgbm)

In [80]:
model.fit(X_train, y_train)

50/50 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 0.5942  


In [81]:
preds = model.predict(X_test)

13/13 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step 


In [98]:
# Define XGBoost model
xgb = MultiOutputRegressor(XGBRegressor(
    n_estimators=500,
    learning_rate=0.05,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42
))

# Define LightGBM model
lgbm = MultiOutputRegressor(LGBMRegressor(
    n_estimators=500,
    learning_rate=0.05,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42
))

# (Optional) Neural Network model, if already trained:
# nn_preds = model.predict(X_test)


In [99]:
xgb.fit(X_train, y_train)
lgbm.fit(X_train, y_train)

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000649 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 12981
[LightGBM] [Info] Number of data points in the train set: 1600, number of used features: 55
[LightGBM] [Info] Start training from score -0.007867
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain

MultiOutputRegressor(estimator=LGBMRegressor(colsample_bytree=0.8,
                                             learning_rate=0.05, max_depth=6,
                                             n_estimators=500, random_state=42,
                                             subsample=0.8))

In [100]:
xgb_preds = xgb.predict(X_test)
lgbm_preds = lgbm.predict(X_test)

# (Optional) if you have neural network predictions
# ensemble_preds = (xgb_preds + lgbm_preds + nn_preds) / 3
ensemble_preds = (xgb_preds + lgbm_preds) / 2
# Create submission DataFrame

In [102]:
# Drop ID column from test_data
X_new = test_data.drop('ID', axis=1)

# Predict with both models
xgb_preds = xgb.predict(X_new)
lgbm_preds = lgbm.predict(X_new)

# Ensemble predictions (simple average — you can change weights)
ensemble_preds = (xgb_preds + lgbm_preds) / 2

# Prepare submission DataFrame
target_columns = [f"BlendProperty{i}" for i in range(1, 11)]
submission = pd.DataFrame(ensemble_preds, columns=target_columns)

# Add ID column at the beginning
submission.insert(0, 'ID', test_data['ID'].values)

# Save to CSV
submission.to_csv('submission.csv', index=False)
print("✅ submission.csv saved.")
# Display submission info
submission.info()

✅ submission.csv saved.
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   ID               500 non-null    int64  
 1   BlendProperty1   500 non-null    float64
 2   BlendProperty2   500 non-null    float64
 3   BlendProperty3   500 non-null    float64
 4   BlendProperty4   500 non-null    float64
 5   BlendProperty5   500 non-null    float64
 6   BlendProperty6   500 non-null    float64
 7   BlendProperty7   500 non-null    float64
 8   BlendProperty8   500 non-null    float64
 9   BlendProperty9   500 non-null    float64
 10  BlendProperty10  500 non-null    float64
dtypes: float64(10), int64(1)
memory usage: 43.1 KB


In [10]:
import numpy as np
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor, GradientBoostingRegressor
from sklearn.svm import SVR
from sklearn.metrics import mean_absolute_percentage_error
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

# === INPUTS ===
X_new = test_data.drop('ID', axis=1)

# === Output Storage ===
all_test_preds_list = []
all_submission_preds_list = []
model_mapes = []

# === Seeds ===
xgb_seeds = [42, 52, 62]
lgbm_seeds = [101, 111, 121]
rf_seeds = [201, 202, 203]
et_seeds = [301, 302, 303]
gbr_seeds = [401, 402, 403]
svr_seeds = [501, 502]  # SVR is slow, fewer runs

# === XGBoost Models (objective: MAE) ===
for seed in xgb_seeds:
    model = XGBRegressor(
        objective='reg:absoluteerror',  # <-- Optimized for MAE
        n_estimators=500,
        learning_rate=0.05,
        max_depth=6,
        subsample=0.8,
        colsample_bytree=0.8,
        random_state=seed,
        n_jobs=-1
    )
    reg = MultiOutputRegressor(model)
    reg.fit(X_train, y_train)

    test_preds = reg.predict(X_test)
    sub_preds = reg.predict(X_new)

    mape = mean_absolute_percentage_error(y_test, test_preds)
    model_mapes.append(mape)
    all_test_preds_list.append(test_preds)
    all_submission_preds_list.append(sub_preds)

# === LightGBM Models (objective: MAE) ===
for seed in lgbm_seeds:
    model = LGBMRegressor(
        objective='mae',  # <-- Optimized for MAE
        n_estimators=500,
        learning_rate=0.05,
        max_depth=6,
        subsample=0.8,
        colsample_bytree=0.8,
        random_state=seed,
        n_jobs=-1
    )
    reg = MultiOutputRegressor(model)
    reg.fit(X_train, y_train)

    test_preds = reg.predict(X_test)
    sub_preds = reg.predict(X_new)

    mape = mean_absolute_percentage_error(y_test, test_preds)
    model_mapes.append(mape)
    all_test_preds_list.append(test_preds)
    all_submission_preds_list.append(sub_preds)

# === Random Forest Models (approximate) ===
for seed in rf_seeds:
    model = RandomForestRegressor(n_estimators=300, max_depth=10, random_state=seed, n_jobs=-1)
    reg = MultiOutputRegressor(model)
    reg.fit(X_train, y_train)

    test_preds = reg.predict(X_test)
    sub_preds = reg.predict(X_new)

    mape = mean_absolute_percentage_error(y_test, test_preds)
    model_mapes.append(mape)
    all_test_preds_list.append(test_preds)
    all_submission_preds_list.append(sub_preds)

# === Extra Trees Models (approximate) ===
for seed in et_seeds:
    model = ExtraTreesRegressor(n_estimators=300, max_depth=10, random_state=seed, n_jobs=-1)
    reg = MultiOutputRegressor(model)
    reg.fit(X_train, y_train)

    test_preds = reg.predict(X_test)
    sub_preds = reg.predict(X_new)

    mape = mean_absolute_percentage_error(y_test, test_preds)
    model_mapes.append(mape)
    all_test_preds_list.append(test_preds)
    all_submission_preds_list.append(sub_preds)

# === Gradient Boosting Models (objective: MAE) ===
for seed in gbr_seeds:
    model = GradientBoostingRegressor(
        n_estimators=300,
        learning_rate=0.05,
        max_depth=6,
        loss='absolute_error',  # <-- Optimized for MAE
        random_state=seed
    )
    reg = MultiOutputRegressor(model)
    reg.fit(X_train, y_train)

    test_preds = reg.predict(X_test)
    sub_preds = reg.predict(X_new)

    mape = mean_absolute_percentage_error(y_test, test_preds)
    model_mapes.append(mape)
    all_test_preds_list.append(test_preds)
    all_submission_preds_list.append(sub_preds)

# === SVR Models (approximate, on subsample) ===
for seed in svr_seeds:
    np.random.seed(seed)
    idx = np.random.permutation(len(X_train))[:2000]  # Subsample for faster training
    model = SVR(C=1.0, epsilon=0.1, kernel='rbf')
    reg = MultiOutputRegressor(model)
    reg.fit(X_train.iloc[idx], y_train.iloc[idx])

    test_preds = reg.predict(X_test)
    sub_preds = reg.predict(X_new)

    mape = mean_absolute_percentage_error(y_test, test_preds)
    model_mapes.append(mape)
    all_test_preds_list.append(test_preds)
    all_submission_preds_list.append(sub_preds)

# === Weighted Ensemble (inversely weighted by MAPE) ===
inv_errors = [1 / (e + 1e-8) for e in model_mapes]  # Avoid div by 0
weights = np.array(inv_errors) / sum(inv_errors)

eval_preds = np.average(np.array(all_test_preds_list), axis=0, weights=weights)
submission_preds = np.average(np.array(all_submission_preds_list), axis=0, weights=weights)

# === Final Evaluation ===
final_mape = mean_absolute_percentage_error(y_test, eval_preds)
print(f"✅ Final Weighted Ensemble MAPE on X_test: {final_mape:.6f}")


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000690 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 12981
[LightGBM] [Info] Number of data points in the train set: 1600, number of used features: 55
[LightGBM] [Info] Start training from score -0.014647
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain

In [12]:

# Target columns
target_columns = [f"BlendProperty{i}" for i in range(1, 11)]

# Create submission DataFrame
submission = pd.DataFrame(submission_preds, columns=target_columns)
submission.insert(0, 'ID', test_data['ID'].values)

# Save to CSV
submission.to_csv("submission.csv", index=False)
print("✅ Dense ensemble saved to submission.csv")


✅ Dense ensemble saved to submission.csv


In [118]:
train_data.shape

(2000, 65)

In [130]:
import numpy as np
import pandas as pd
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import HistGradientBoostingRegressor
from sklearn.metrics import mean_absolute_percentage_error
from sklearn.model_selection import KFold

from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor

# === Parameters ===
n_splits = 5
seeds = [42, 52, 62]
X_new = test_data.drop('ID', axis=1)

# === Containers ===
submission_preds_list = []
eval_preds_list = []

# === K-Fold Cross-Validation ===
kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)

for seed in seeds:
    for fold, (train_idx, val_idx) in enumerate(kf.split(X_train)):
        print(f"🔁 Seed {seed} | Fold {fold+1}/{n_splits}")
        
        X_tr, X_val = X_train.iloc[train_idx], X_train.iloc[val_idx]
        y_tr, y_val = y_train.iloc[train_idx], y_train.iloc[val_idx]

        # Models to train
        models = {
            'XGB': XGBRegressor(n_estimators=300, learning_rate=0.05, max_depth=6, n_jobs=-1, random_state=seed),
            'LGBM': LGBMRegressor(n_estimators=300, learning_rate=0.05, max_depth=6, n_jobs=-1, random_state=seed),
            'CAT': CatBoostRegressor(n_estimators=300, learning_rate=0.05, depth=6, random_state=seed, verbose=0),
            'HGB': HistGradientBoostingRegressor(max_iter=300, learning_rate=0.05, max_depth=6, random_state=seed)
        }

        for name, base_model in models.items():
            model = MultiOutputRegressor(base_model)
            model.fit(X_tr, y_tr)

            # Predict on test set (X_test) and future test data (X_new)
            eval_preds_list.append(model.predict(X_test))
            submission_preds_list.append(model.predict(X_new))


🔁 Seed 42 | Fold 1/5
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000772 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 12979
[LightGBM] [Info] Number of data points in the train set: 1280, number of used features: 55
[LightGBM] [Info] Start training from score -0.019848
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

In [131]:
# Average predictions from all models
submission_preds = np.mean(submission_preds_list, axis=0)
eval_preds = np.mean(eval_preds_list, axis=0)

# MAPE Evaluation
mape = mean_absolute_percentage_error(y_test, eval_preds)
print(f"✅ MAPE on X_test: {mape:.6f}")


✅ MAPE on X_test: 1.581490


In [133]:
target_columns = [f"BlendProperty{i}" for i in range(1, 11)]
submission = pd.DataFrame(submission_preds, columns=target_columns)
submission.insert(0, 'ID', test_data['ID'].values)
submission.to_csv("submission.csv", index=False)
print("📁 Saved: submission.csv")


📁 Saved: submission.csv


In [15]:
pip install smogn

Note: you may need to restart the kernel to use updated packages.


In [18]:
y_train

BlendProperty1  BlendProperty2  BlendProperty3  BlendProperty4  \
968        -0.981309        0.858009        0.029339        0.367219   
240         1.990971        1.836163        0.397096        0.827889   
819         0.771757        0.526459        0.090594        1.332086   
692         0.238978        1.054073        0.365554        1.110819   
420         1.244411        1.184151        0.459951        1.945102   
...              ...             ...             ...             ...   
1130        0.113478       -0.192621        0.003512        1.313949   
1294       -1.744809       -1.410379       -0.531553       -0.938615   
860        -0.298812       -0.294033        0.768053       -0.213151   
1459        0.418281        0.768766        1.567564        1.564234   
1126        0.148074        0.158671        0.869763       -0.365499   

      BlendProperty5  BlendProperty6  BlendProperty7  BlendProperty8  \
968         0.042194        0.776438        0.018815        1.081787   
240         1.072529        1.022516        0.379908        0.421323   
819        -0.296572        1.179951        0.079077        1.061006   
692        -0.185477        0.375349        0.348825        1.085592   
420        -1.358725       -0.107867        0.441596        0.206778   
...              ...             ...             ...             ...   
1130       -1.206053        0.299131       -0.006400        0.640551   
1294       -0.211680       -0.340611       -0.531466       -0.242947   
860        -0.266626       -0.390918        0.743696       -0.871070   
1459        1.775462        1.081005        1.528363        0.901927   
1126        1.331082        0.744769        0.843603        0.727481   

      BlendProperty9  BlendProperty10  
968         0.031999        -1.148377  
240         0.129762        -0.397750  
819         2.042837        -0.136298  
692         1.063145         1.701030  
420         0.954062         1.870651  
...              ...              ...  
1130        0.525061         1.386984  
1294       -0.777379        -1.716578  
860        -0.732099        -0.346396  
1459        0.993424         1.133930  
1126        0.205529         1.136408  

[1600 rows x 10 columns]

In [17]:
import smogn
df = pd.concat([X_train, y_train], axis=1)

df_balanced = smogn.smoter(
    data=df,
    y='y',  # Only 1 target column supported
    samp_method='extreme'
)

# Split back into X, y
X_res = df_balanced.drop('y', axis=1)
y_res = df_balanced['y']


KeyError: 'y'

In [21]:
list(columns) + [target_columns[0]]

['Component1_fraction',
 'Component2_fraction',
 'Component3_fraction',
 'Component4_fraction',
 'Component5_fraction',
 'Component1_Property1',
 'Component2_Property1',
 'Component3_Property1',
 'Component4_Property1',
 'Component5_Property1',
 'Component1_Property2',
 'Component2_Property2',
 'Component3_Property2',
 'Component4_Property2',
 'Component5_Property2',
 'Component1_Property3',
 'Component2_Property3',
 'Component3_Property3',
 'Component4_Property3',
 'Component5_Property3',
 'Component1_Property4',
 'Component2_Property4',
 'Component3_Property4',
 'Component4_Property4',
 'Component5_Property4',
 'Component1_Property5',
 'Component2_Property5',
 'Component3_Property5',
 'Component4_Property5',
 'Component5_Property5',
 'Component1_Property6',
 'Component2_Property6',
 'Component3_Property6',
 'Component4_Property6',
 'Component5_Property6',
 'Component1_Property7',
 'Component2_Property7',
 'Component3_Property7',
 'Component4_Property7',
 'Component5_Property7',
 'Com

In [25]:
import pandas as pd
import numpy as np
from smogn import smoter

# Assuming your data is in a DataFrame called 'data'
# with features X and targets y1, y2, ..., y10
columns = list(X_train.columns)
df = pd.concat([X_train,y_train], axis=1)
results = {}
for target_col in target_columns:
    
    # Create temporary dataset with features + single target
    temp_data = df[columns  + [target_col]].copy()  # replace with your actual feature names

    rrel_ctrl_pts_rg = [
    [min(temp_data[target_col]), 0],
    [some_normal_value, 0],
    [some_rare_value, 1],
    [max(temp_data[target_col]), 0]
    ]

    smogn_data = smoter(
    data=temp_data,
    y=target_col,
    k=5,
    pert=0.02,
    samp_method='balance',
    rel_method='manual',
    rel_ctrl_pts_rg=rel_ctrl_pts_rg,
    drop_na_col=True,
    drop_na_row=True
    )

    
    results[target_col] = smogn_data

# You can then combine results or use them separately

NameError: name 'some_normal_value' is not defined